# Surface map of METAR data

## Objective
> In this notebook, we will make a surface map based on current observations from METAR sites across North America.

In [ ]:
from datetime import datetime,timedelta
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import cartopy.crs as ccrs
import cartopy.feature as cfeature

from metpy.calc import wind_components, reduce_point_density
from metpy.units import units
from metpy.plots import StationPlot
from metpy.plots.wx_symbols import current_weather, sky_cover, wx_code_map

In [ ]:
# Load in a collection of functions that process GEMPAK weather conditions and cloud cover data.
%run /kt11/ktyle/python/metargem.py

## Determine the date and hour to gather observations <a class="anchor" id="step2"></a>

In [ ]:
# Use the current time, or set your own for a past time.
# Set current to False if you want to specify a past time.

nowTime = datetime.utcnow()
#current = True
current = False
if (current):
    validTime = datetime.utcnow()
    year = validTime.year
    month = validTime.month
    day = validTime.day
    hour = validTime.hour
else:
    year = 2024
    month = 3
    day = 23
    hour = 23
    
validTime = datetime(year, month, day, hour)
deltaTime = nowTime - validTime
deltaDays = deltaTime.days

timeStr = validTime.strftime("%Y-%m-%d %H UTC")
timeStr2 = validTime.strftime("%Y%m%d%H")
YYMMDDHH = validTime.strftime("%y%m%d%H")
print(timeStr)
print(validTime)
print(deltaTime)
print(deltaDays)

### The METAR data are in hourly CSV files which can be opened by Pandas.<a class="anchor" id="step3a"></a>
[Top](#top)

In [ ]:
metarFile = f'/ktyle_rit/scripts/sflist2/complete/{YYMMDDHH}.csv'
df = pd.read_csv(metarFile, sep="\s+")

In [ ]:
df

### Set the domain to gather data from and for defining the plot region.

In [ ]:
latN = 55
latS = 20
lonW = -125
lonE = -60

cLat = (latN + latS)/2
cLon = (lonW + lonE )/2

Perform the spatial subset. Extend the data bounds slightly.

In [ ]:
extend = 0.01
df2 = df.query('SLAT >= (@latS - @extend) & SLAT <= (@latN + @extend) & SLON  >= (@lonW - @extend) & SLON <= (@lonE + @extend)')

<div class="alert alert-info">
    <b>Note:</b> We're using a different Pandas function, <a href="https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.query.html">query</a>, to perform our subset. Its syntax is similar to that used in databases. Note how we phrase columns and previously-defined variables!</div>

In [ ]:
df2

Select the weather variables of interest. Also include the site ID, lat, lon, elevation, and time columns.

In [ ]:
columnSubset = ['STN', 'YYMMDD/HHMM', 'SLAT', 'SLON', 'SELV', 'TMPC', 'DWPC', 'PMSL',
                'SKNT', 'DRCT','ALTI','WNUM','VSBY','CHC1', 'CHC2', 'CHC3','CTYH', 'CTYM', 'CTYL']

In [ ]:
df3 = df2[columnSubset]

In [ ]:
df3

In these datasets, -9999.0 signfies missing values. Replace all instances of -9999.0 with NumPy's `NaN` (not a number) value.

In [ ]:
df4 = df3.replace(-9999.0, np.nan)

In [ ]:
df4

In [ ]:
data = df4

In our current data archive, multiple weather types are often not represented properly. To avoid a type conversion error, set stations whose weather type fall into this category to missing.

*This will eventually be fixed!*

In [ ]:
data.loc[data['WNUM'] =='********', ['WNUM']] = '-9999.00'
data['WNUM'] = data['WNUM'].astype('float16')

#### Read in several of the columns as Pandas `Series`; extract the value arrays from the `Series` objects; assign / convert units as necessary; convert GEMPAK cloud cover and present wx symbols to MetPy's representation 

In [ ]:
lats = data['SLAT'].values
lons = data['SLON'].values
tair = (data['TMPC'].values * units ('degC')).to('degF')
dewp = (data['DWPC'].values * units ('degC')).to('degF')
altm = (data['ALTI'].values * units('inHg')).to('mbar')
slp = data['PMSL'].values * units('hPa')

# Convert wind to components
u, v = wind_components(data['SKNT'].values * units.knots, data['DRCT'].values * units.degree)

# replace missing wx codes or those >= 100 with 0, and convert to MetPy's present weather code
wnum = (np.nan_to_num(data['WNUM'].values,True).astype(int))
convert_wnum (wnum)

# Need to handle missing (NaN) and convert to proper code
chc1 = (np.nan_to_num(data['CHC1'].values,True).astype(int))
chc2 = (np.nan_to_num(data['CHC2'].values,True).astype(int))
chc3 = (np.nan_to_num(data['CHC3'].values,True).astype(int))
cloud_cover = calc_clouds(chc1, chc2, chc3)

# For some reason station id's come back as bytes instead of strings. This line converts the array of station id's into an array of strings.
#stid = np.array([s.decode() for s in data['station']])
stid = data['STN']


The next step deals with the removal of overlapping stations, using  `reduce_point_density`. This returns a mask we can apply to data to filter the points.

Select a Cartopy map projection, which we will use both to reduce plotted station density and to plot the data on a map.

In [ ]:
# Uncomment whichever projection you want (or add your own!)
# proj = ccrs.Stereographic(central_longitude=cLon, central_latitude=cLat)
proj = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)

In [ ]:
# Project points so that we're filtering based on the way the stations are laid out on the map

xy = proj.transform_points(ccrs.PlateCarree(), lons, lats)

# Reduce point density so that there's only one point within a circle whose distance is specified in meters.
# This value will need to change depending on how large of an area you are plotting.
density = 150000
mask = reduce_point_density(xy, density)

<div class="alert alert-info">
    <b>Note:</b> In the call to <code>transform_points</code>, we pass in the arrays of the stations' longitudes and latitudes. Since their units are in degrees, we need to also specify their corresponding map projection ... which is <b>PlateCarree</b> for degrees of longitude and latitude.</div>

## Visualize Surface Observations <a class="anchor" id="viz"></a>
[Top](#top)

#### Simple station plotting using plot methods

One way to create station plots with MetPy is to create an instance of `StationPlot` and call various plot methods, like `plot_parameter`, to plot arrays of data at locations relative to the center point.

In addition to plotting values, `StationPlot` has support for plotting text strings, symbols, and plotting values using custom formatting.

Plotting symbols involves mapping integer values to various custom font glyphs in our custom weather symbols font. MetPy provides mappings for converting WMO codes to their appropriate symbol. The `sky_cover` and `current_weather` functions below are two such mappings.

Now we just plot with `arr[mask]` for every `arr` of data we use in plotting.

In [ ]:
# Set up a plot with map features
# First set dpi ("dots per inch") - higher values will give us a less pixelated final figure.
dpi = 125

fig = plt.figure(figsize=(24,18), dpi=dpi)

ax = fig.add_subplot(1, 1, 1, projection=proj) # We use the projection defined above
ax.set_facecolor(cfeature.COLORS['water'])

land_mask = cfeature.NaturalEarthFeature('physical', 'land', '50m',
                                        edgecolor='face',
                                        facecolor=cfeature.COLORS['land'])
lake_mask = cfeature.NaturalEarthFeature('physical', 'lakes', '50m',
                                        edgecolor='face',
                                        facecolor=cfeature.COLORS['water'])
state_borders = cfeature.NaturalEarthFeature(category='cultural', name='admin_1_states_provinces_lakes',
                                         scale='50m', facecolor='none')

ax.add_feature(land_mask)
ax.add_feature(lake_mask)
ax.add_feature(state_borders, linestyle='solid', edgecolor='black')

# Slightly reduce the extent of the map as compared to the subsetted data region; this helps eliminate data from being plotted beyond the frame of the map
ax.set_extent ((lonW+2,lonE-4,latS+1,latN-2), crs=ccrs.PlateCarree())
ax.set_extent ((lonW+0.2,lonE-0.2,latS+.1,latN-.1), crs=ccrs.PlateCarree())
ax.set_extent ((lonW,lonE,latS,latN), crs=ccrs.PlateCarree())

#If we wanted to add grid lines to our plot:
#ax.gridlines()

# Create a station plot pointing to an Axes to draw on as well as the location of points
stationplot = StationPlot(ax, lons[mask], lats[mask], transform=ccrs.PlateCarree(),
                          fontsize=8)

stationplot.plot_parameter('NW', tair[mask], color='red', fontsize=10)
stationplot.plot_parameter('SW', dewp[mask], color='darkgreen', fontsize=10)

# Below, we are using a custom formatter to control how the sea-level pressure
# values are plotted. This uses the standard trailing 3-digits of the pressure value
# in tenths of millibars.
stationplot.plot_parameter('NE', slp[mask], color='purple', formatter=lambda v: format(10 * v, '.0f')[-3:])



stationplot.plot_symbol('C', cloud_cover[mask], sky_cover)
stationplot.plot_symbol('W', wnum[mask], current_weather,color='blue',fontsize=12)
stationplot.plot_text((2, 0),stid[mask], color='gray')
#zorder - Higher value zorder will plot the variable on top of lower value zorder. This is necessary for wind barbs to appear. Default is 1.
stationplot.plot_barb(u[mask], v[mask],zorder=2)

plotTitle = (f"Sfc Map valid at:  {timeStr}")
ax.set_title (plotTitle);

In [ ]:
# In order to see the entire figure, type the name of the figure object below.
fig

In [ ]:
figName = (f'{timeStr2}_sfmap.png')
fig.savefig(figName)